<a href="https://colab.research.google.com/github/navjotsingh151/CarModelPredictionApp/blob/master/CarClassifier.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Car Model Classification

This app uses Stanford Car data to predict the model , make, company of the car.

Dataset is available [here](https://ai.stanford.edu/~jkrause/cars/car_dataset.html)

[Link](https://ai.stanford.edu/~jkrause/papers/3drr13.pdf) to the white paper

# Data and Library Import 

In [1]:
import pandas as pd

from fastai.vision import *
from fastai.metrics import error_rate
from scipy.io import loadmat

In [2]:
!wget http://ai.stanford.edu/~jkrause/cars/car_devkit.tgz
!tar xvzf car_devkit.tgz

## main Data file
!wget http://imagenet.stanford.edu/internal/car196/car_ims.tgz

--2020-06-22 22:34:37--  http://ai.stanford.edu/~jkrause/cars/car_devkit.tgz
Resolving ai.stanford.edu (ai.stanford.edu)... 171.64.68.10
Connecting to ai.stanford.edu (ai.stanford.edu)|171.64.68.10|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 330960 (323K) [application/x-gzip]
Saving to: ‘car_devkit.tgz’

car_devkit.tgz      100%[===================>] 323.20K   472KB/s    in 0.7s    

2020-06-22 22:34:38 (472 KB/s) - ‘car_devkit.tgz’ saved [330960/330960]

devkit/
devkit/cars_meta.mat
devkit/cars_train_annos.mat
devkit/cars_test_annos.mat
devkit/README.txt
devkit/train_perfect_preds.txt
devkit/eval_train.m


In [13]:
%%bash
wget http://imagenet.stanford.edu/internal/car196/cars_train.tgz
wget http://imagenet.stanford.edu/internal/car196/cars_test.tgz

rm -R dataset/
mkdir dataset
tar zxvf cars_train.tgz -C /content/dataset/
tar zxvf cars_test.tgz -C /content/dataset/

--2020-06-22 22:49:27--  http://imagenet.stanford.edu/internal/car196/cars_train.tgz
Resolving imagenet.stanford.edu (imagenet.stanford.edu)... 171.64.68.16
Connecting to imagenet.stanford.edu (imagenet.stanford.edu)|171.64.68.16|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 979269282 (934M) [application/x-gzip]
Saving to: ‘cars_train.tgz’

     0K .......... .......... .......... .......... ..........  0%  122K 2h10m
    50K .......... .......... .......... .......... ..........  0%  243K 98m9s
   100K .......... .......... .......... .......... ..........  0%  365K 80m0s
   150K .......... .......... .......... .......... ..........  0%  366K 70m54s
   200K .......... .......... .......... .......... ..........  0%  726K 61m6s
   250K .......... .......... .......... .......... ..........  0%  723K 54m35s
   300K .......... .......... .......... .......... ..........  0%  728K 49m55s
   350K .......... .......... .......... .......... ..........  0%  730K 4

In [14]:
%%bash
ls -l /content/dataset/cars_train/ | wc -l
ls -l /content/dataset/cars_test/ | wc -l


cars_train/
cars_train/00001.jpg
cars_train/00002.jpg
cars_train/00003.jpg
cars_train/00004.jpg
cars_train/00005.jpg
cars_train/00006.jpg
cars_train/00007.jpg
cars_train/00008.jpg
cars_train/00009.jpg
cars_train/00010.jpg
cars_train/00011.jpg
cars_train/00012.jpg
cars_train/00013.jpg
cars_train/00014.jpg
cars_train/00015.jpg
cars_train/00016.jpg
cars_train/00017.jpg
cars_train/00018.jpg
cars_train/00019.jpg
cars_train/00020.jpg
cars_train/00021.jpg
cars_train/00022.jpg
cars_train/00023.jpg
cars_train/00024.jpg
cars_train/00025.jpg
cars_train/00026.jpg
cars_train/00027.jpg
cars_train/00028.jpg
cars_train/00029.jpg
cars_train/00030.jpg
cars_train/00031.jpg
cars_train/00032.jpg
cars_train/00033.jpg
cars_train/00034.jpg
cars_train/00035.jpg
cars_train/00036.jpg
cars_train/00037.jpg
cars_train/00038.jpg
cars_train/00039.jpg
cars_train/00040.jpg
cars_train/00041.jpg
cars_train/00042.jpg
cars_train/00043.jpg
cars_train/00044.jpg
cars_train/00045.jpg
cars_train/00046.jpg
cars_train/00047.jpg
c

In [16]:
unpack_double = lambda x: x[0][0]
unpack_single = lambda x: x[0]
im_path = '/content/dataset/'

def prepare_df(path, singles = [], doubles = []):
    annos = loadmat(path)['annotations']
    df = pd.DataFrame(annos[0])
    
    for item in singles:
        df[item] = df[item].apply(unpack_single)
    
    for item in doubles:
        df[item] = df[item].apply(unpack_double)

    return df[singles + doubles]

train = prepare_df('devkit/cars_train_annos', ['fname'], ['class'])
test = prepare_df('devkit/cars_test_annos', ['fname'])

train['name'] = train['fname'].apply(lambda name: im_path+'cars_train/' + name)
test['name'] = test['fname'].apply(lambda name: im_path+'cars_test/' + name)

del train['fname']
del test['fname']

train['class'] = train['class'].apply(lambda x: x-1)

meta = pd.DataFrame(loadmat('devkit/cars_meta.mat')['class_names'][0], columns=['class_name'])
meta['class_name'] = meta['class_name'].apply(unpack_single)

train['label'] = train['class'].apply(lambda x: meta.iloc[x].class_name)
del train['class']

In [17]:
train.head()

name                                label
0  /content/dataset/cars_train/00001.jpg                  Audi TTS Coupe 2012
1  /content/dataset/cars_train/00002.jpg                  Acura TL Sedan 2012
2  /content/dataset/cars_train/00003.jpg           Dodge Dakota Club Cab 2007
3  /content/dataset/cars_train/00004.jpg     Hyundai Sonata Hybrid Sedan 2012
4  /content/dataset/cars_train/00005.jpg  Ford F-450 Super Duty Crew Cab 2012

In [6]:
data = ImageDataBunch.from_df('', train, ds_tfms=get_transforms(), size=224, bs=64).normalize(imagenet_stats)
data

FileNotFoundError: ignored